# 4.2 Modelado de un Vehículo de Transmisión Diferencial (Duckiebot)

## Tabla de Contenidos
1. Introducción a los Modelos Matemáticos
2. Representación del Estado
3. Cinemática (Directa e Inversa)
4. Modelo del Motor DC

---

## 1. Introducción a los Modelos Matemáticos

Un **modelo matemático** es una representación abstracta de un sistema real que captura las relaciones causales entre sus componentes, específicamente mapeando las variables de **Entrada (Inputs)** a las de **Salida (Outputs)**.

### 1.1 Objetivos del Modelado
No buscamos una descripción exacta de la realidad, sino cuantificar variables esenciales para:
* **Predicción:** Anticipar el comportamiento futuro del sistema (e.g., estimación de pose).
* **Control:** Manipular las entradas ($u_t$) para gobernar la dinámica y obtener la salida deseada.

### 1.2 Tipología de Modelos
1.  **Basados en Datos (Data-Driven / Black-box):**
    * Aprenden la correlación entrada-salida a partir de datasets (experiencia) sin conocimiento explícito de la física subyacente.
    * *Ejemplo:* Redes neuronales (como se ve en la primera imagen del diagrama).
2.  **Basados en Principios Físicos (Mecanicistas / White-box):**
    * Derivados de leyes fundamentales (ej. 2da Ley de Newton, Leyes de Kirchhoff). Son deterministas y explicables.
    * *Ejemplo:* El diagrama de bloques de control clásico.

---

### 1.3 Representación en Espacio de Estados
En este curso, nos centraremos en modelos físicos descritos mediante ecuaciones de estado generales:

$$
\dot{x}_t = f(x_t, u_t)
$$

$$
y_t = g(x_t, u_t) 
$$

Donde:
* $x_t$: **Vector de Estado** (variables internas mínimas para describir el sistema).
* $u_t$: **Vector de Control** (entradas, e.g., voltajes).
* $y_t$: **Vector de Salida** (mediciones o variables de interés).

<div align="center">
    <img src="imagenes/Pasted image 20260209205921.png" alt="Modelo basado en datos (Red Neuronal)" width="500"/>
    <p><em>Fig 1. Modelo basado en datos (Red Neuronal) vs. Modelo Físico</em></p>
    <br>
    <img src="imagenes/models.png" alt="Diagrama de bloques del sistema físico" width="700"/>
    <p><em>Fig 2. Esquema de control basado en modelo físico</em></p>
</div>

## 2. Plataforma: El Robot de Accionamiento Diferencial (Duckiebot)

El Duckiebot opera bajo una topología de **accionamiento diferencial**, donde el movimiento se logra mediante la diferencia de velocidades entre dos ruedas motrices independientes.

### 2.1 Configuración Física y Flujo de Señales
El sistema convierte energía eléctrica en movimiento espacial a través de la siguiente cadena de transformación:

1.  **Entrada (Control):** Voltajes $V_{l,t}, V_{r,t}$ aplicados a los motores DC.
2.  **Dinámica del Actuador:** Generación de Torque ($\tau$) y consecuente Velocidad Angular ($\dot{\phi}_{l,t}, \dot{\phi}_{r,t}$) en las ruedas.
3.  **Cinemática:** La interacción rueda-suelo transforma el giro en velocidad lineal y angular del chasis.
4.  **Salida (Estado):** Evolución del vector de Pose $\mathbf{q}_t = [x, y, \theta]^T$.

<div align="center">
    <img src="imagenes/Pasted image 20260209202936.png" alt="Esquema Differential Drive" width="600"/>
    <p><em>Fig 3. Diagrama de bloques: De Voltaje a Pose</em></p>
</div>

### 2.2 Preguntas Fundamentales

Esta sección define los dos problemas principales de la robótica móvil aplicados al Duckiebot:

**1. (Cinemática Directa)** Dados las velocidades de las ruedas $\dot{\phi}_1, \dot{\phi}_2, \dots, \dot{\phi}_t$, ¿cómo se moverá el robot en el espacio $(x, y, \theta)$?

**2. (Cinemática Inversa)** Dado un movimiento o trayectoria deseada $(q_1, \dots, q_t)$, ¿qué comandos (velocidades o voltajes) debemos enviar a las ruedas?

### 2.3 Notaciones y Suposiciones

Para modelar el movimiento matemáticamente, definimos los marcos de referencia y las restricciones físicas del sistema.

* **Marco Global (World Frame):** $\{x^w, y^w\}$ — Fijo en el entorno.
* **Marco del Cuerpo (Body/Robot Frame):** $\{x^r, y^r\}$ — Se mueve con el robot.

#### Suposición 1: Simetría
El robot es simétrico a lo largo del eje longitudinal ($x^r$).
* Las ruedas están equidistantes del centro (longitud del eje = $2L$).
* Las ruedas son idénticas (radio $R_l = R_r = R$).
* El centro de masa se encuentra en el eje $x^r$ a una distancia $c$ desde el punto $A$.

#### Suposición 2: Cuerpo Rígido
El robot se comporta como un cuerpo rígido ideal.
* La distancia entre dos puntos cualesquiera del robot no cambia con el tiempo.
* Matemáticamente: $\dot{c} = 0$, donde $(\dot{\star}) = \frac{d(\star)}{dt}$.

<div align="center">
    <img src="imagenes/Pasted image 20260209203048.png" alt="Diagrama del chasis del robot" width="500"/>
</div>

## 3. Cinemática y Geometría del Robot

Antes de formular las ecuaciones de movimiento, debemos definir los problemas a resolver y la geometría del sistema.

### 3.1 Problemas Fundamentales
Buscamos establecer las relaciones matemáticas para responder a dos necesidades de ingeniería:
1.  **Cinemática Directa (Predicción):** Dados los estados de los actuadores (velocidades de rueda $\dot{\phi}$), determinar la evolución del robot en el espacio $(\dot{x}, \dot{y}, \dot{\theta})$.
2.  **Cinemática Inversa (Control):** Dada una velocidad deseada del chasis, calcular las consignas de control para cada motor.

### 3.2 Marcos de Referencia y Pose
Para cuantificar el movimiento, definimos dos marcos ortonormales:
* **Marco Global ($\{W\}$):** Sistema inercial fijo en el entorno $(x_W, y_W)$.
* **Marco del Cuerpo ($\{R\}$):** Sistema móvil solidario al chasis $(x_R, y_R)$.

La **Pose** ($\mathbf{q}_t$) define el estado completo del vehículo en el plano:
$$\mathbf{q}_t = [x_t, y_t, \theta_t]^T \in SE(2)$$

### 3.3 Suposiciones Geométricas (Topología)
Basado en el diagrama del chasis, asumimos un **Cuerpo Rígido** con simetría longitudinal:
* **Punto $A$ (Centro de Eje):** Origen del marco $\{R\}$, equidistante a las ruedas.
* **Punto $C$ (Centro de Masa):** Ubicado en el eje longitudinal $x_R$, desplazado una distancia $c$ respecto a $A$.
* **Parámetros:**
    * $R$: Radio de las ruedas (asumido idéntico).
    * $L$: Semiancho de vía (distancia lateral de $A$ a la rueda).

<div align="center">
    <img src="imagenes/Pasted image 20260209203048.png" alt="Geometría del Duckiebot y Marcos de Referencia" width="600"/>
</div>

### 4. Ecuaciones Cinemáticas Generales

Una vez que entendemos cómo se mueven las ruedas, debemos traducir ese movimiento al **Marco Global**. Esto se logra mediante la matriz de rotación $R(\theta)$.

#### Transformación de Velocidades
La velocidad del punto de referencia $A$ en el mundo ($\mathbf{v}_A^w$) se relaciona con la velocidad en el marco del robot ($\mathbf{v}_A^r$) rotando el vector por el ángulo actual $\theta$:

$$
\mathbf{v}_A^w = \begin{bmatrix} \dot{x} \\ \dot{y} \end{bmatrix} = R(\theta) \mathbf{v}_A^r = \underbrace{\begin{bmatrix} \cos\theta & -\sin\theta \\ \sin\theta & \cos\theta \end{bmatrix}}_{R(\theta)} \begin{bmatrix} v_u \\ v_v - c\dot{\theta} \end{bmatrix}
$$

De esto obtenemos el **Sistema de Ecuaciones Cinemáticas**:

$$
\begin{cases} 
\dot{x} = v_u \cos\theta - (v_v - c\dot{\theta}) \sin\theta \\ 
\dot{y} = v_u \sin\theta + (v_v - c\dot{\theta}) \cos\theta \\ 
\dot{\theta} = \omega 
\end{cases}
$$

Donde $\omega$ es la velocidad angular del chasis alrededor del eje $z$.

### 5. Restricciones Cinemáticas

Para que el modelo sea válido en Duckietown (y en la mayoría de robots de ruedas), asumimos condiciones de "rodadura ideal".

#### 1. Sin Deslizamiento Lateral (No Skidding)
El robot no puede deslizarse de lado (como un coche derrapando en hielo). Esto implica que la velocidad lateral en el punto de contacto es cero.
$$
\mathbf{v}_A^r = \begin{bmatrix} v_u \\ 0 \end{bmatrix} \quad \Rightarrow \quad v_v = c\dot{\theta}
$$
*(Si el centro de masa está en el eje de las ruedas, $c=0$, entonces $v_v=0$).*

#### 2. Sin Patinaje de Rueda (No Slipping)
La rueda no gira en falso. En cada revolución completa ($\Delta\phi = 2\pi$), la rueda avanza exactamente su perímetro ($\Delta x = 2\pi R$).

La relación fundamental entre la velocidad lineal de la rueda ($v_{l/r}$) y su velocidad angular ($\dot{\phi}_{l/r}$) es:

$$
v_{l/r} = \frac{\Delta x}{\Delta t} = \dot{\phi}_{l/r} R
$$

<div align="center">
    <img src="imagenes/Pasted image 20260209203302.png" alt="Relación velocidad angular y lineal" width="600"/>
    <p><em>Fig 4. Relación geométrica entre velocidad angular y lineal</em></p>
</div>

## 6. Centro Instantáneo de Curvatura (ICC)

Debido a la naturaleza diferencial del movimiento, el robot rota instantáneamente alrededor de un punto pivote en el espacio llamado **ICC** (*Instantaneous Center of Curvature*).

### 6.1 Análisis Geométrico
La velocidad angular del chasis ($\omega$) es idéntica para todo el cuerpo rígido, pero la velocidad lineal ($v$) depende de la distancia al ICC.

* **Variables:**
    * $d$: Distancia desde el centro del eje ($A$) al ICC.
    * $L$: Semiancho de vía (distancia de $A$ a la rueda).
* **Relación de Velocidades:**
    $$v_{izq} = \omega (d - L)$$
    $$v_{der} = \omega (d + L)$$

### 6.2 Derivación del Radio de Curvatura ($d$)
Resolviendo el sistema anterior para $d$ y $\omega$, obtenemos la geometría del giro en función de las velocidades de las ruedas:

**Velocidad Angular del Robot:**
$$\omega = \frac{v_{der} - v_{izq}}{2L}$$

**Radio de Curvatura ($d$):**
$$d = L \frac{v_{der} + v_{izq}}{v_{der} - v_{izq}}$$

### 6.3 Casos Especiales (Interpretación)
* **Línea Recta ($v_{der} = v_{izq}$):** El denominador se hace cero, $d \to \infty$. El ICC está en el infinito.
* **Rotación en el Sitio ($v_{der} = -v_{izq}$):** El numerador se hace cero, $d = 0$. El ICC coincide con el punto $A$.
* **Pivote ($v_{izq} = 0$):** El robot gira con centro en la rueda estática.

<div align="center">
    <img src="imagenes/Pasted image 20260209203752.png" alt="Geometría del ICC y velocidades" width="400"/>
</div>

## 7. Modelos Cinemáticos: Directo e Inverso

A partir de la geometría y las restricciones, derivamos los dos modelos fundamentales para la operación del robot.

### 7.1 Cinemática Directa (Forward Kinematics)
**Problema:** Estimación de Estado / Odometría.
*Pregunta:* Dada una velocidad medida en las ruedas ($\dot{\varphi}_r, \dot{\varphi}_l$), ¿cuál es la velocidad resultante del chasis en el espacio?

La velocidad lineal ($v$) es el promedio de las velocidades tangenciales, mientras que la velocidad angular ($\omega$) es proporcional a su diferencia:

$$v = \frac{r}{2} (\dot{\varphi}_r + \dot{\varphi}_l)$$

$$\omega = \frac{r}{2L} (\dot{\varphi}_r - \dot{\varphi}_l)$$

### 7.2 Cinemática Inversa (Inverse Kinematics)
**Problema:** Control de Movimiento.
*Pregunta:* Si deseo una velocidad lineal ($v$) y angular ($\omega$) específica, ¿qué consignas de velocidad debo enviar a cada motor?

Este sistema se obtiene invirtiendo algebraicamente las ecuaciones anteriores:

$$\dot{\varphi}_r = \frac{v + \omega L}{r}$$

$$\dot{\varphi}_l = \frac{v - \omega L}{r}$$

### 8. Integración: Del Voltaje a la Pose (Duckiebot Model)

Finalmente, combinamos el modelo de los actuadores (Motores DC) con la geometría del robot para obtener el modelo completo de **Cinemática Directa**.

El objetivo es encontrar la evolución del estado $\dot{\mathbf{q}}_t$ basándonos en los voltajes de entrada $V_{l,t}$ y $V_{r,t}$.

<div align="center">
    <img src="imagenes/Pasted image 20260209211407.png" alt="Modelo completo del Duckiebot" width="800"/>
</div>

#### Ecuación Matricial Completa

La evolución del sistema se describe multiplicando las matrices de rotación y geometría:

$$
\dot{\mathbf{q}}_t = \underbrace{\frac{R}{2} \begin{bmatrix} 
\cos\theta & 0 \\ 
\sin\theta & 0 \\ 
0 & 1 
\end{bmatrix}}_{\text{Transformación a Marco Global}} 
\underbrace{\begin{bmatrix} 
1 & 1 \\ 
\frac{1}{L} & -\frac{1}{L} 
\end{bmatrix}}_{\text{Geometría del Chasis}} 
\begin{bmatrix} 
\dot{\phi}_r \\ 
\dot{\phi}_l 
\end{bmatrix}
$$

Donde las velocidades de las ruedas $\dot{\phi}$ se obtienen del modelo del motor que vimos anteriormente:

$$
\dot{\phi}_t = \left( R \frac{b}{K_i} + K_b \right)^{-1} V_t
$$

**Interpretación de las matrices:**
1.  **Matriz derecha:** Convierte las velocidades individuales de las ruedas en velocidad lineal ($v$) y angular ($\omega$) del robot.
2.  **Matriz izquierda:** Proyecta esas velocidades ($v, \omega$) en las coordenadas globales $(x, y, \theta)$ usando la orientación actual.

In [3]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.patches as patches
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

# --- 1. TU LÓGICA DE CINEMÁTICA (Intacta) ---
def forward_kinematics(phi_dot_left, phi_dot_right, theta, R, L):
    """
    Calcula [x_dot, y_dot, theta_dot] usando las matrices de la teoría.
    """
    wheel_speeds = np.array([[phi_dot_right], [phi_dot_left]])
    
    # Matriz de Geometría (Ruedas -> v, omega)
    # R/2 se aplica fuera, pero la estructura es la misma
    geometry_matrix = np.array([
        [1, 1],
        [1/L, -1/L]
    ])
    
    # Matriz de Rotación (Local -> Global)
    rotation_matrix = np.array([
        [np.cos(theta), 0],
        [np.sin(theta), 0],
        [0, 1]
    ])
    
    # Cinemática Directa: q_dot = (R/2) * Rot * Geom * Wheels
    robot_frame_vels = (R / 2) * np.dot(geometry_matrix, wheel_speeds)
    global_vels = np.dot(rotation_matrix, robot_frame_vels)
    
    return global_vels.flatten()

# --- 2. CLASE PARA VISUALIZACIÓN ---
class DuckiebotVisualizer:
    def __init__(self):
        # Parámetros físicos (Duckiebot)
        self.R = 0.0318  # Radio rueda
        self.L = 0.05    # Baseline/2
        self.dt = 0.1    # Paso de tiempo de simulación
        
        # Estado inicial [x, y, theta]
        self.state = np.array([0.0, 0.0, 0.0])
        
        # Historial para dibujar la estela (trayectoria)
        self.history_x = [0.0]
        self.history_y = [0.0]

        # Configuración de la gráfica
        self.fig, self.ax = plt.subplots(figsize=(8, 8))
        self.ax.set_xlim(-1, 2)
        self.ax.set_ylim(-1, 2)
        self.ax.set_aspect('equal')
        self.ax.grid(True, linestyle='--', alpha=0.6)
        self.ax.set_title("Cinemática Diferencial: Visualización en Tiempo Real")
        self.ax.set_xlabel("Mundo X [m]")
        self.ax.set_ylabel("Mundo Y [m]")

        # Elementos gráficos
        self.trail, = self.ax.plot([], [], 'b--', alpha=0.5, label='Trayectoria')
        # Cuerpo del robot (rectángulo amarillo)
        self.body = patches.Rectangle((-0.06, -0.05), 0.12, 0.1, color='#FFD700', alpha=0.9, label='Chasis')
        # Ruedas (negros)
        self.wheel_l = patches.Rectangle((-0.03, 0.05), 0.06, 0.015, color='black')
        self.wheel_r = patches.Rectangle((-0.03, -0.065), 0.06, 0.015, color='black')
        # Flecha de dirección
        self.arrow = self.ax.quiver(0, 0, 1, 0, scale=10, color='r', width=0.005)
        
        # Texto de info
        self.info_text = self.ax.text(0.05, 0.95, '', transform=self.ax.transAxes, 
                                      verticalalignment='top', bbox=dict(boxstyle='round', facecolor='white', alpha=0.8))

        # Añadir parches
        self.ax.add_patch(self.body)
        self.ax.add_patch(self.wheel_l)
        self.ax.add_patch(self.wheel_r)

    def update(self, frame):
        # --- DEFINIR ENTRADAS (VELOCIDADES DE RUEDA) ---
        # Simulamos una secuencia: Recto -> Giro Izquierda -> Giro Derecha fuerte
        if frame < 20:
            wl, wr = 10.0, 10.0  # Recto
            mode = "Recta (v_izq = v_der)"
        elif frame < 50:
            wl, wr = 8.0, 12.0   # Giro suave izquierda
            mode = "Curva (v_der > v_izq)"
        else:
            wl, wr = 12.0, 2.0   # Giro cerrado derecha
            mode = "Giro (v_izq >> v_der)"

        # --- APLICAR TU FUNCIÓN DE CINEMÁTICA ---
        # Obtenemos las derivadas (velocidades)
        q_dot = forward_kinematics(wl, wr, self.state[2], self.R, self.L)
        
        # --- INTEGRACIÓN NUMÉRICA (Euler) ---
        # Nueva Posición = Posición Vieja + Velocidad * Tiempo
        self.state += q_dot * self.dt
        
        # Guardar historial
        self.history_x.append(self.state[0])
        self.history_y.append(self.state[1])

        # --- ACTUALIZAR GRÁFICOS ---
        x, y, theta = self.state

        # 1. Actualizar estela
        self.trail.set_data(self.history_x, self.history_y)

        # 2. Transformación para rotar y mover el cuerpo del robot
        # Creamos una matriz de transformación afín para mover los parches
        t = plt.matplotlib.transforms.Affine2D().rotate(theta).translate(x, y) + self.ax.transData
        
        self.body.set_transform(t)
        self.wheel_l.set_transform(t)
        self.wheel_r.set_transform(t)

        # 3. Flecha de dirección (vector de velocidad local x)
        self.arrow.set_offsets([x, y])
        self.arrow.set_UVC(np.cos(theta), np.sin(theta))

        # 4. Actualizar texto
        info = (f"Modo: {mode}\n"
                f"Entradas: wL={wl:.1f}, wR={wr:.1f} rad/s\n"
                f"Estado: x={x:.2f}, y={y:.2f}\n"
                f"Orientación: {np.degrees(theta):.1f}°\n"
                f"Vel Lineal calc: {q_dot[0]/np.cos(theta) if np.cos(theta)!=0 else 0:.2f} m/s")
        self.info_text.set_text(info)

        # Ajustar cámara si el robot se sale
        if x > self.ax.get_xlim()[1] - 0.5:
            self.ax.set_xlim(self.ax.get_xlim()[0]+0.1, self.ax.get_xlim()[1]+0.1)
        if y > self.ax.get_ylim()[1] - 0.5:
            self.ax.set_ylim(self.ax.get_ylim()[0]+0.1, self.ax.get_ylim()[1]+0.1)
            
        return self.body, self.wheel_l, self.wheel_r, self.trail, self.arrow, self.info_text

# 1. Crear la instancia
viz = DuckiebotVisualizer()

# 2. Crear la animación
# Nota: guardamos en variable 'anim'
anim = FuncAnimation(viz.fig, viz.update, 
                     frames=np.arange(0, 100), 
                     interval=50, 
                     blit=False)

# 3. Renderizar como HTML interactivo
# Esto genera un reproductor de video en la celda
plt.close() # Evita que se duplique la gráfica estática
HTML(anim.to_jshtml())

### 9 Dinámica Detallada de los Motores (Subsistemas)

<div align="center">     <img src="imagenes/DC_motor_intuition.png" alt="Intuición del Motor DC" width="800"/> </div>

Un motor DC es un convertidor de energía. Transforma energía eléctrica en energía mecánica.

**El Estator (Stator):** Es la parte estática externa que aloja imanes permanentes (Norte y Sur). Su función es crear un campo magnético fijo.

**El Rotor:** Es la parte interna que gira, compuesta por bobinas de alambre conectadas al eje.

Cuando aplicamos un voltaje, fluye una corriente a través de las bobinas del rotor. Esta corriente, al interactuar con el campo magnético del estator, genera una fuerza física (Fuerza de Lorentz) que empuja la bobina, creando el Torque necesario para girar la rueda."

<div align="center">
    <img src="imagenes/Screenshot 2026-02-10 120713.png" alt="Modelo completo del Duckiebot" width="800"/>
</div>

Para un control de bajo nivel más preciso, no solo miramos la velocidad final, sino cómo llegamos a ella. Esto implica considerar el comportamiento eléctrico (inductancia) y mecánico (inercia).

#### Subsistema Eléctrico
Relaciona el voltaje con la corriente, considerando la resistencia y la inductancia de la bobina:

$$
V_t = R i_t + L_e \frac{di_t}{dt} + K_b \dot{\phi}_t
$$

* $K_b \dot{\phi}_t$: **Fuerza contraelectromotriz (Back e.m.f.)**. Voltaje generado por el propio giro del motor que se opone a la entrada.
* $\tau_t = K_i i_t$: El torque generado es proporcional a la corriente.

#### Subsistema Mecánico
Relaciona el torque con la aceleración angular, considerando la inercia del rotor y la fricción:

$$
J \ddot{\phi}_t = \tau_t - b \dot{\phi}_t
$$

* $J$: Inercia del rotor.
* $b \dot{\phi}_t$: **Fricción viscosa**.

## 10. Conclusiones y Resumen (Takeaways)

Como cierre de esta unidad de modelado, consolidamos las tres ecuaciones maestras que gobiernan la dinámica del Duckiebot. Estas herramientas matemáticas son la base para los algoritmos de navegación y control.

### 10.1 Hoja de Referencia de Ecuaciones

| Modelo | Ecuación | Aplicación |
| :--- | :--- | :--- |
| **1. Cinemática Directa** | $\dot{\mathbf{q}}_t = \frac{R}{2} \begin{bmatrix} \cos\theta & 0 \\ \sin\theta & 0 \\ 0 & 1 \end{bmatrix} \begin{bmatrix} 1 & 1 \\ \frac{1}{L} & -\frac{1}{L} \end{bmatrix} \begin{bmatrix} \dot{\phi}_r \\ \dot{\phi}_l \end{bmatrix}$ | **Odometría:** Estimar la posición futura basada en sensores. |
| **2. Cinemática Inversa** | $\begin{bmatrix} \dot{\phi}_r \\ \dot{\phi}_l \end{bmatrix} = \frac{1}{R} \begin{bmatrix} 1 & L \\ 1 & -L \end{bmatrix} \begin{bmatrix} v \\ \omega \end{bmatrix}$ | **Control:** Calcular comandos de motor para seguir una trayectoria. |
| **3. Modelo Actuador (DC)** | $\dot{\phi}_t = \left( R \frac{b}{K_i} + K_b \right)^{-1} V_t$ | **Hardware:** Relación física entre Voltaje (Software) y Velocidad Mecánica. |

### 10.2 Glosario de Parámetros
* **$\mathbf{q}_t = [x, y, \theta]^T$:** Vector de Pose en el Marco Global.
* **$\dot{\phi}_{r, l}$:** Velocidad angular de ruedas derecha/izquierda [rad/s].
* **$R$:** Radio de la rueda [m].
* **$L$:** Semiancho de vía (mitad de la distancia entre ruedas) [m].
* **$v, \omega$:** Velocidad lineal y angular del chasis.

### 10.3 Limitaciones del Modelo
Recordemos la máxima de George Box: *"Todos los modelos son incorrectos, pero algunos son útiles"*. Este modelo asume condiciones ideales que no siempre se cumplen en la realidad:
1.  **Suelo plano y tracción perfecta** (Sin deslizamiento).
2.  **Parámetros constantes** ($R$ y $L$ no cambian, aunque los neumáticos se deformen).
3.  **Motores idénticos** (Asume simetría eléctrica perfecta).